# 03-Clustering Map

This notebook has the aim of producing an HTML page that shows the location of all schools in Trentino. In addition to that, hover and on-click information about schools are inserted and well formatted. For instance, emails, website and phone numbers are clickable, making it easy to reach the institution. Also, since there are over 700 schools, i.e. 700 points, the map will be clustered, such that when zooming out points inside a specific area are grouped together, which makes the map more readable. 

In [1]:
import folium
import pandas as pd
import geopandas as gpd
from folium.plugins import MarkerCluster
import branca

Let's read the dataset saved in geojson and convert main information to title (first letter uppercase).

In [2]:
schools = gpd.read_file("../data/trentino/schools/schools.geojson")
schools[['Istituto', 'Nome', 'Comune']] = schools[[
    'Istituto', 'Nome', 'Comune']].applymap(lambda x: x.title())

The following function generates the popup that appears when clicking on a Marker representing a school. It generates a HTML document containing the school name as heading and a table containing:

* Institute;
* Type of school (i.e. grade);
* Management (private or private);
* Address;
* Municipality;
* CAP;
* Whenever present, inserts the links to emails, fax, phone number and website.

In [3]:
def generate_popup(row):
    # Open the HTML popup table
    text = """
        <!DOCTYPE html>
        <html>
            <style>
                @import url('https://fonts.googleapis.com/css2?family=Roboto:ital,wght@0,100;0,400;0,500;1,300;1,400;1,700&display=swap');
            </style>
            <h4 style="font-family: 'Roboto', sans-serif;">{}</h4>
            <table style="height: 150px; width: 350px; font-family: 'Roboto', sans-serif;">
            <tbody>
        """.format(row['Nome'])

    # Iterate over columns
    for c in ['Istituto', 'Tipo Istituto', 'Gestione',
              'Indirizzo', 'Comune', 'CAP', 'Telefono', 'Fax',
              'Email istituto', 'Email segreteria', 'Sito web']:

        # If the value is Null, don't insert it in the table
        if row[c] != None:
            if c in ['Sito web']:
                # Insertion of clickable links
                text = text + """
                <tr>
                    <td><b>{}</b></td>
                    <td><a href = "https://{}" target="_blank">{}</a></td>""".format(c, row[c], row[c]) + """
                </tr>
                """
            elif c in ['Telefono', 'Fax']:
                # Insertion of clickable links
                text = text + """
                <tr>
                    <td><b>{}</b></td>
                    <td><a href = "tel:{}" target="_blank">{}</a></td>""".format(c, row[c], row[c]) + """
                </tr>
                """
            elif 'Email' in c:
                # Insertion of clickable links
                text = text + """
                <tr>
                    <td><b>{}</b></td>
                    <td><a href = "mailto:{}" target="_blank">{}</a></td>""".format(c, row[c], row[c]) + """
                </tr>
                """
            else:  # No need for links
                text = text + """
                    <tr>
                        <td><b>{}</b></td>
                        <td>{}</td>""".format(c, row[c]) + """
                    </tr>
                """

    # Close the table
    text = text + """
            </tbody>
            </table>
        </html>
        """
    return text

We now import the geopackage from Github, selecting the municipalities layer. The Trento Province has code 22, therefore we select a subset of the dataset for Trentino. EPSG 4326 is set as CRS and then we get the entire Trentino's territory by dissolving the municipalities. 

In [4]:
# Importing Trentino GeoData
url = 'https://github.com/napo/geospatial_course_unitn/blob/master/data/istat/istat_administrative_units_generalized_2021.gpkg?raw=true'
trentino = gpd.read_file(url, layer="municipalities")
trentino = trentino[trentino['COD_PROV'] == 22]
trentino = trentino.to_crs(4326)
trentino = trentino.dissolve(by="COD_PROV")

In [5]:
trentino.explore()

The following chunk actually creates and then saves the map, centered in Trento.
Initially, no tiles are present such that it is possible to select them from the Layer Control in the upper right part of the map. 

Then, Trentino boundary is inserted, without including its area (for better readability of data). Schools are inserted in "Scuole" FeatureGroup, such that it can be added to the MarkerCluster and allow the clustering/de-clustering of points when zooming in/out. It is possible to deselect both Trentino's boundary and Schools' Markers from the Layer Control. 

Whenever schools' markers are added to the feature group, the popup is generated from the function described above. 

In the end, a Search bar is inserted in the map, allowing to search any school according to the school's name. 

In [7]:
# CLUSTERING MAP
map = folium.Map(location=[46.0904, 11.14], zoom_start=9, tiles=None)

# Adding layers
folium.TileLayer("cartodbpositron", name="Light", show=True).add_to(map)
folium.TileLayer("Cartodb dark_matter", name="Dark").add_to(map)
folium.TileLayer('openstreetmap', name="OpenStreetMap").add_to(map)

# Adding Trentino Boundary
style = {'fillColor': 'rgba(255,255,255,0)', 'color': '#DD696D'}
tn = folium.FeatureGroup(name='Trentino', show=True)
folium.GeoJson(trentino.to_json(), 
               style_function=lambda x:style).add_to(tn)
map.add_child(tn)


# Adding cluster of points
fg = folium.FeatureGroup(name='Scuole', show=True)
cluster = MarkerCluster(icon_create_function="""
    function (cluster) {    
        var childCount = cluster.getChildCount();  
        if (childCount < 20) {  
            c = '#FEDB71'
        } else if (childCount < 40) {  
            c = '#FEB85D' 
        } else if (childCount < 100) {  
            c = '#EE8A59';  
        } else { 
            c = '#DD696D'  
        }    
        return new L.DivIcon({ html: '<div style="background-color:'+c+'"><span>' + childCount + '</span></div>', className: 'marker-cluster', iconSize: new L.Point(40, 40) });

  }
  """).add_to(fg)
map.add_child(fg)

# Tile Layer control
folium.LayerControl().add_to(map)

# Adding points to clusters
for p in schools.iterrows():
    text = generate_popup(p[1])
    iframe = branca.element.IFrame(html=text, width=400, height=280)
    popup = folium.Popup(folium.Html(text, script=True), max_width=400)
    folium.Marker([p[1]['geometry'].y, p[1]['geometry'].x],
                  icon=folium.map.Icon(prefix='fa',
                                       icon='graduation-cap',
                                       color="lightred"),
                  popup=popup,
                  name = p[1]['Nome'],
                  tooltip=p[1]['Nome']).add_to(cluster)
    
#Add search bar
from folium.plugins import Search
servicesearch = Search(
    layer=cluster,
    search_label='name',
    search_zoom=18,
    placeholder='Cerca una scuola...',
    collapsed=True).add_to(map)

map
#map.save('../viz/schools_cluster.html')